In [43]:
import json

dataset_synthetic_scores = []
with open('/home/firouzi/embedding_model/data_preprocess_notebook/data/synthetic-persian-qa-retrieval/train.jsonl', 'r', encoding='utf-8') as f:
    for line in f:
        data = json.loads(line)
        dataset_synthetic_scores.append(data)

dataset_synthetic_queries = {}
with open('/home/firouzi/embedding_model/data_preprocess_notebook/data/synthetic-persian-qa-retrieval/queries.jsonl', 'r', encoding='utf-8') as f:
    for line in f:
        json_data = json.loads(line)
        dataset_synthetic_queries[json_data['_id']] = json_data

dataset_synthetic_corpus = {}
with open('/home/firouzi/embedding_model/data_preprocess_notebook/data/synthetic-persian-qa-retrieval/corpus.jsonl', 'r', encoding='utf-8') as f:
    for line in f:
        json_data = json.loads(line)
        dataset_synthetic_corpus[json_data['_id']] = json_data

print(len(dataset_synthetic_scores))
print(len(dataset_synthetic_queries))
print(len(dataset_synthetic_corpus))

1000212
250666
270642


In [44]:
all_dataset = {}
for data_topic in dataset_synthetic_scores:
    
    query_id = data_topic['query-id']
    corpus_id = int(data_topic['corpus-id'])
    score = data_topic['score']

    if (query_id in dataset_synthetic_queries) and (corpus_id in dataset_synthetic_corpus):
        if score == "1":
            if query_id in all_dataset:
                all_dataset[query_id]['passgae_positive'].append(dataset_synthetic_corpus[corpus_id]['text'])
            else:
                all_dataset[query_id] = {'question': dataset_synthetic_queries[query_id]['text'], 
                                         'passgae_positive': [dataset_synthetic_corpus[corpus_id]['text']], 
                                         'passgae_negative': [], 
                                         'passage_negative_random': []}
        else:
            if query_id in all_dataset:
                all_dataset[query_id]['passgae_negative'].append(dataset_synthetic_corpus[corpus_id]['text'])
            else:
                all_dataset[query_id] = {'question': dataset_synthetic_queries[query_id]['text'], 
                                         'passgae_positive': [],
                                         'passgae_negative': [dataset_synthetic_corpus[corpus_id]['text']],
                                         'passage_negative_random': []}


all_dataset = list(all_dataset.values())
print(len(all_dataset))

223423


In [45]:
all_dataset[71]

{'question': 'چه کسانی باید کتاب لوازم نویسندگی را بخوانند؟',
 'passgae_positive': ['این کتاب به ویژه برای علاقه مندان تازه کار به هنر داستان نویسی مفید است. افرادی که مشتاق یادگیری نمایشنامه، فیلمنامه، حکایت یا قصه هستند می توانند از این راهنمای کاربردی بهره ببرند.'],
 'passgae_negative': ['این کتاب در دسته بندی پژوهش ادبی، مجموعه آموزش نویسندگی قرار می گیرد. همچنین این کتاب به عنوان یک نقشه راه برای افرادی که ایده ای را پرورش داده اند و قصد دارند آن را با قلمی رسا بیان کنند، پیشنهاد شده است.',
  'این کتاب به ویژه برای افرادی که در حوزه ادبیات کودک فعالیت می\u200cکنند یا قصد ورود به این حوزه را دارند، مفید و سازنده است. خواندن این کتاب می\u200cتواند به نویسندگان کمک کند تا با بازار نویسندگی برای کودکان آشنا شوند و مهارت\u200cهای لازم برای نوشتن آثار مناسب برای این گروه سنی را کسب کنند.',
  "کتاب 'همه چیز درباره نویسندگی خلاق' نکات کلیدی و چالش\u200cهای مختلفی را برای نویسندگان تازه\u200cکار ارائه می\u200cدهد. این نکات شامل تکنیک\u200cهای فرّار برای غلبه بر خشک\u200cطبعی در نویسندگی، م

In [48]:
import requests
from dotenv import load_dotenv
import os
import re

load_dotenv()

qwen = False
if qwen:
    url = "https://qwen3.chatllm.aiengines.ir/v1/chat/completions"
    model = "Qwen/Qwen3-4B-Instruct-2507"
    headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('LLM_AS_RERANKER_PASS')}"}
else:
    url = "http://192.168.130.206:4001/v1/chat/completions"
    model = "google/gemma-3-27b-it"
    headers = {"Content-Type": "application/json"}

instruction = """
You are a helpful assistant that help me to find that the text is relevant to the question or not.
You are given a question and a text.
You must evaluate the text based on the question and return "1" if the text is relevant to the question and "0" if the text is not relevant to the question.
 
be carefull, I have chosen the text randomly from my dataset so the text must answer the question independently.
You must return the result in the following format:
{{"result": "1" or "0"}}
"""


id = 7850

print("question:")
print(all_dataset[id]["question"])
print("--------------------------------")
print("passgae_positive:")
print(all_dataset[id]["passgae_positive"][0])
print("--------------------------------")
for i in range(len(all_dataset[id]["passgae_negative"])):
    question, passgae_negative = all_dataset[id]['question'], all_dataset[id]["passgae_negative"][i]
    input_message = f"""{{"question": "{question}", "text": "{passgae_negative}"}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 100
    }

    req = requests.post(url, headers=headers, json=payload)
    print(all_dataset[id]["passgae_negative"][i])
    print(req.json()['choices'][0]['message']['content'])
    out = req.json()['choices'][0]['message']['content']
        
    match = re.search(r'"result":\s*([\d\.]+)', out)

    if match:
        result = match.group(1)
    print(result)
    print("--------------------------------")

question:
چگونه خنده می‌تواند به کاهش استرس کمک کند؟
--------------------------------
passgae_positive:
خنده به عنوان یک واکنش طبیعی بدن، می‌تواند به کاهش سطح هورمون‌های استرس مانند کورتیزول کمک کند. تحقیقی از دانشگاه کانزاس نشان داده است که خندیدن در شرایط استرس‌زا، ضربان قلب افراد را کاهش می‌دهد و به آنها احساس آرامش بیشتری می‌دهد. این اثرات مثبت به ویژه در خنده‌های اجتماعی مشهود است، که نشان می‌دهد حتی لبخند زدن نیز می‌تواند به کاهش استرس کمک کند.
--------------------------------
خندیدن به اشتباهات می‌تواند به عنوان یک مکانیزم مقابله‌ای عمل کند که به افراد کمک می‌کند تا با فشارهای روانی و استرس‌های روزمره کنار بیایند. این عمل نه تنها به کاهش تنش‌های عاطفی کمک می‌کند، بلکه می‌تواند به بهبود روابط اجتماعی نیز منجر شود. در واقع، افرادی که قادر به خندیدن به اشتباهات خود هستند، معمولاً احساس راحتی بیشتری در تعاملات اجتماعی دارند و می‌توانند به راحتی با دیگران ارتباط برقرار کنند.
{{"result": "1"}}


NameError: name 'result' is not defined

In [50]:
out

'{{"result": "1"}}'

In [53]:
import re

out = '{"result": "1"}'
match = re.search(r'"result":\s*"?([\d\.]+)"?', out)


result = match.group(1)

print(result)

1


In [57]:
r = [""]
if not r:
    print("empty")